<a href="https://colab.research.google.com/github/PraveenMishraJi/main/blob/main/Final_Copy.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [20]:
!pip install chromadb -q
!pip install sentence-transformers -q

In [21]:
import chromadb

client = chromadb.Client()

In [22]:
import os
import json

documents = []
metadatas = []
ids = []

with open(os.path.join('newIdeas.json'), 'r') as file:
    data = json.load(file)  # Load the JSON data from the file

    for item in data:
        ids.append(item["ids"])  # Append 'ids' to the 'ids' list
        metadatas.append(item["title"])  # Append 'title' to the 'metadatas' list
        documents.append(item["desc"])  # Append 'desc' to the 'documents' list
        print(ids,metadatas,documents)


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [23]:
import chromadb
import chromadb.config
from chromadb.config import Settings
client = chromadb.PersistentClient(
    path="idea_db")

In [24]:
#client.delete_collection("idea_collection")

ValueError: ignored

In [25]:
idea_collection = client.create_collection("idea_collection")
idea_collection.add(
    documents=documents,
    metadatas=metadatas,
    ids=ids
)

In [26]:
results = idea_collection.query(
    query_texts=["hotel food"],
    n_results=1
)
results

{'ids': [['id180']],
 'distances': [[0.9975849390029907]],
 'metadatas': [[{'Cultural Exchange': 'International Food Festivals'}]],
 'embeddings': None,
 'documents': [['Host international food festivals showcasing global cuisines. Promote culinary diversity and cultural exchange through delicious dishes.']]}

# **This is the trouble section**
#### So i am trying to add custom transformers to chromadb and to create embeddings and it is not working

In [27]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('paraphrase-MiniLM-L3-v2')

In [28]:
import os
import json

documents = []
metadatas = []
ids = []

with open(os.path.join('newIdeas.json'), 'r') as file:
    data = json.load(file)  # Load the JSON data from the file

    for item in data:
        ids.append(item["ids"])  # Append 'ids' to the 'ids' list
        metadatas.append(item["title"])  # Append 'title' to the 'metadatas' list
        documents.append(item["desc"])  # Append 'desc' to the 'documents' list
        print(ids,metadatas,documents)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [29]:
embeddings = []
embeding = model.encode(documents).tolist()  # Use item['documents'] to access the 'documents' key
embeddings.extend(embeding)

In [30]:
documents

['Establish AI communities in Abu Dhabi to transform the city into an AI hub for future technologies. Attract AI talent, foster innovation, and collaborate with tech companies to drive advancements in artificial intelligence.',
 "Plant trees along roadways to reduce sun heat and provide shade. Enhance the city's aesthetics, improve air quality, and create cooler outdoor spaces for residents and visitors to enjoy.",
 'Invest in improving security measures in public places to prevent incidents and maintain the safety and hygiene of Dubai and populous areas. Ensure a safe and welcoming environment for residents and tourists.',
 'Launch urban reforestation projects to plant more trees and reduce temperatures. Enhance the urban landscape, reduce the reliance on air conditioning, and create a greener and more sustainable city.',
 'Subsidize CNG (Compressed Natural Gas) vehicles to promote fuel efficiency and reduce pollution. Encourage the adoption of eco-friendly transportation options, mak

In [31]:
embeddings

[[-0.3176901936531067,
  -0.1332012116909027,
  0.10172418504953384,
  0.05182582885026932,
  -0.019876403734087944,
  -0.05624803155660629,
  0.14856700599193573,
  -0.3371811807155609,
  0.01987985149025917,
  0.263801634311676,
  0.09069855511188507,
  -0.23602981865406036,
  0.1118178591132164,
  -0.04289769008755684,
  0.1468513458967209,
  0.23558726906776428,
  0.24040880799293518,
  0.0152696268633008,
  0.17221441864967346,
  -0.2625983655452728,
  -0.014772417023777962,
  -0.3524162173271179,
  -0.11716003715991974,
  -0.22054269909858704,
  0.043397240340709686,
  -0.00520490575581789,
  0.10160734504461288,
  -0.1755189299583435,
  -0.05229545757174492,
  -0.04827466979622841,
  0.2039840668439865,
  0.169272318482399,
  0.2251022756099701,
  -0.005428831093013287,
  -0.17263320088386536,
  0.2534242272377014,
  0.02183632366359234,
  0.09419701248407364,
  -0.01662822999060154,
  -0.3653528094291687,
  0.12034058570861816,
  -0.05723853036761284,
  0.30741453170776367,
  0

In [34]:
client.delete_collection("idea_collection_emb")

In [35]:
idea_collection_emb = client.create_collection("idea_collection_emb")
idea_collection_emb.add(
    documents=documents,
    embeddings=embeddings,
    metadatas=metadatas,
    ids=ids
)

In [52]:
import numpy as np

# Function to calculate similarity score from L2 distance
def calculate_similarity(distance):
    # You can use a function like this to convert L2 distance to similarity percentage
    # You may need to adjust this formula depending on your specific requirements
    similarity_score = (1 / (1 + distance))*1000  # Adjust the formula as needed
    similarity_score = round(similarity_score, 2)
    return similarity_score

query = input("Please enter your suggestion: ")
input_em = model.encode(query).tolist()

# Perform the query using ChromaDB
results = idea_collection_emb.query(
    query_embeddings=[input_em],
    n_results=3,
    include=["distances", "metadatas", "documents"]
)

# Assuming that the 'results' dictionary contains distances, metadatas, and documents
distances = results.get("distances", [])
metadatas = results.get("metadatas", [])
documents = results.get("documents", [])

print(query)

# Check if distances are available and non-empty
if distances and len(distances[0]) > 0:
    # Combine distances, metadatas, and documents into tuples
    result_tuples = zip(distances[0], metadatas[0], documents[0])

    # Calculate similarity scores and sort the results by increasing distances
    sorted_results = sorted(result_tuples, key=lambda x: x[0], reverse=False)

    # Extract the sorted metadatas, documents, and similarity scores
    sorted_metadatas = [metadata for _, metadata, _ in sorted_results]
    sorted_documents = [document for _, _, document in sorted_results]
    similarity_scores = [calculate_similarity(distance) for distance, _, _ in sorted_results]

    # Print the sorted metadatas, documents, and similarity scores
    for i, (metadata, document, similarity_score) in enumerate(zip(sorted_metadatas, sorted_documents, similarity_scores), start=1):
        print(f"Result {i}:")
        print("Metadata:", metadata)
        print("Similarity Score: {}%".format(similarity_score))
        print("Document:", document)
        print()

else:
    print("No results found.")


Please enter your suggestion: none
none
Result 1:
Metadata: {'Sustainable Practices': 'Zero-Waste Initiatives'}
Similarity Score: 17.54%
Document: Launch zero-waste initiatives to minimize waste generation. Promote recycling, composting, and sustainable consumption.

Result 2:
Metadata: {'Sustainable Practices': 'Zero-Waste Initiatives'}
Similarity Score: 17.25%
Document: Promote zero-waste initiatives to reduce landfill waste. Encourage recycling, composting, and sustainable consumption.

Result 3:
Metadata: {'Education Excellence': 'STEM Learning Centers'}
Similarity Score: 16.37%
Document: Create STEM (Science, Technology, Engineering, and Mathematics) learning centers for students. Foster innovation and prepare the next generation for tech-driven careers.



#Code Testing Area


In [56]:
import numpy as np

# Function to calculate similarity score from L2 distance
def calculate_similarity(distance):
    # You can use a function like this to convert L2 distance to similarity percentage
    # You may need to adjust this formula depending on your specific requirements
    similarity_score = (1 / (1 + distance))*1000  # Adjust the formula as needed
    similarity_score = round(similarity_score, 2)
    return similarity_score

query = input("Please enter your suggestion: ")
input_em = model.encode(query).tolist()

# Perform the query using ChromaDB
results = idea_collection_emb.query(
    query_embeddings=[input_em],
    n_results=3,
    include=["distances", "metadatas", "documents"]
)

# Assuming that the 'results' dictionary contains distances, metadatas, and documents
distances = results.get("distances", [])
metadatas = results.get("metadatas", [])
documents = results.get("documents", [])

print(query)

# Check if distances are available and non-empty
if distances and len(distances[0]) > 0:
    # Combine distances, metadatas, and documents into tuples
    result_tuples = zip(distances[0], metadatas[0], documents[0])

    # Calculate similarity scores and sort the results by increasing distances
    sorted_results = sorted(result_tuples, key=lambda x: x[0], reverse=False)

    # Extract the sorted metadatas, documents, and similarity scores
    sorted_metadatas = [metadata for _, metadata, _ in sorted_results]
    sorted_documents = [document for _, _, document in sorted_results]
    similarity_scores = [calculate_similarity(distance) for distance, _, _ in sorted_results]

    # Print the sorted metadatas, documents, and similarity scores
    for i, (metadata, document, similarity_score) in enumerate(zip(sorted_metadatas, sorted_documents, similarity_scores), start=1):
      if similarity_score > 25:
        print(f"Result {i}:")
        print("Metadata:", metadata)
        print("Similarity Score: {}%".format(similarity_score))
        print("Document:", document)
        print()
      else:
        print("nice idea")

else:
    print("No results found.")


Please enter your suggestion: 3eqenq3q3
3eqenq3q3
nice idea
nice idea
nice idea


In [37]:
import numpy as np

# Function to calculate similarity score from L2 distance
def calculate_similarity(distance):
    # You can use a function like this to convert L2 distance to similarity percentage
    # You may need to adjust this formula depending on your specific requirements
    similarity_score = (1 / (1 + distance))*1000  # Adjust the formula as needed
    similarity_score = round(similarity_score, 2)
    return similarity_score
title = []
query = input("Please enter your suggestion description: ")
input_em = model.encode(query).tolist()

# Perform the query using ChromaDB
results = idea_collection_emb.query(
    query_embeddings=[input_em],
    n_results=3,
    include=["distances", "metadatas", "documents"]
)

# Assuming that the 'results' dictionary contains distances, metadatas, and documents
distances = results.get("distances", [])
metadatas = results.get("metadatas", [])
documents = results.get("documents", [])

print(query)

# Check if distances are available and non-empty
if distances and len(distances[0]) > 0:
    # Combine distances, metadatas, and documents into tuples
    result_tuples = zip(distances[0], metadatas[0], documents[0])

    # Calculate similarity scores and sort the results by increasing distances
    sorted_results = sorted(result_tuples, key=lambda x: x[0], reverse=False)

    # Extract the sorted metadatas, documents, and similarity scores
    sorted_metadatas = [metadata for _, metadata, _ in sorted_results]
    sorted_documents = [document for _, _, document in sorted_results]
    similarity_scores = [calculate_similarity(distance) for distance, _, _ in sorted_results]

    # Print the sorted metadatas, documents, and similarity scores
    for i, (metadata, document, similarity_score) in enumerate(zip(sorted_metadatas, sorted_documents, similarity_scores), start=1):
          #If the similarity_scores is above 10% then only the results will show
        if similarity_scores[0] > 10:
            print("similarity_score",type(similarity_score),type(similarity_scores))
            print(f"Result {i}:")
            print("Metadata:", metadata)
            print("Similarity Score: {}%".format(similarity_score))
            print("Document:", document)
            print()
        else:
          add_items = input('Your input is unique, \n \t Do you wish to add it to new Ideas Press "Y" for Yes or "N" for No:')
          title = input("Please tell me title of your suggestion and category")
          query = input("Please describe your suggestion once again: ")
          if add_items == "Y" or "y":
            print("the feature is not available yet")
          else: print("thank you for using the program")

else:
    print("No results found.")


list

# **Making program awesome**

In [ ]:
import json
import os

def get_highest_id(existing_data):
    highest_id = 0
    for entry in existing_data:
        try:
            entry_id = int(entry.get("ids", "").replace("id", ""))
            if entry_id > highest_id:
                highest_id = entry_id
        except ValueError:
            pass
    return highest_id

def main():
    ideas_file = "ideas.json"
    new_ideas_file = "newIdeas.json"

    # Check if the "ideas.json" file exists
    if os.path.exists(ideas_file):
        # Load existing data from "ideas.json"
        with open(ideas_file, "r") as f:
            existing_data = json.load(f)
    else:
        # Create a new empty list if "ideas.json" doesn't exist
        existing_data = []

    # Check if the "newIdeas.json" file exists
    if os.path.exists(new_ideas_file):
        # Load existing data from "newIdeas.json"
        with open(new_ideas_file, "r") as f:
            new_ideas_data = json.load(f)
    else:
        # Create a new empty list if "newIdeas.json" doesn't exist
        new_ideas_data = []

    highest_id = max(get_highest_id(existing_data), get_highest_id(new_ideas_data))

    while True:
        title = input("Enter the title: ")
        category = input("Enter the category: ")
        description = input("Enter the description: ")

        highest_id += 1
        new_entry = {
            "ids": f"id{highest_id}",
            "title": {category: title},
            "desc": description
        }

        existing_data.append(new_entry)

        with open(ideas_file, "w") as f:
            json.dump(existing_data, f, indent=2)

        print("Entry added to ideas.json.")

        choice = input("Do you want to add another entry? (Y/N): ")
        if choice.lower() != "y":
            break

if __name__ == "__main__":
    main()
